# Review Opinion Ectraction
This is a tutorial of my recent semantic clustering work. The purpose is to extract opinion phrases from the reviews and make clustering to find the most typical opinions. THe product reviews data are from amazon.com. The schema of is like the below:

1. Data clean and preprossing, especially filtering with opinion lexicon
2. Extract opinions based on Part of Speech(POS) rules
2. Apply Word Mover's distance based on Glove and Word2vec, and cluster them 
3. Finally we will compare the revelence accuracy of two method


**After importing packages, you can skip the parts 1, 2 since they are very time consuming**

### 1. Data Collection and Processing
- data scrapy

### 2. Extract opinion 
- POS ONLY
- POS and dependency analysis
- candidate generate(filter low frequencies?)
- Rough(Recall-Oriented Understudy for Gisting Evaluation) to evaluate

### 3. Semantic similarity calculation and clustering
- WMD distance + Glove
- WMD distance + word2vec

### 4. Result analysis and Hypothesis Test
Get accuracies first.
#### 4.1 Check Assumptions
- 1.Outliers: from the boxplot, we can find there is no outliers.
- 2.Normal Distribution: From the QQ-PLOT, we can find the difference follows the normal distribution.
#### 4.2 Hypostheis test and Power analysis
- Total there will be nine pairs of data point, after power analysis, when the effect size is 1.4, and significance level of 0.05, we can be 80% claim our experiments are reliable. 
- The null hypothesis is that there is no difference between accuracies between the two methods, while the alternative hypothesis is there is some difference. Statics of paired sample t test will be utilized here. After assumption check and hypothesis test, we got the p-value of 0.936, which is much larger than 0.05, the significance level, so that we do not reject null hypothesis and conclude that there is no significant difference between the accuracies between clustering models based on word2vec and glove embeddings.


In [17]:
import os
import glob
import re
import itertools
from collections import Counter
from nltk.tokenize import word_tokenize
import gensim
from gensim.models import KeyedVectors 
from gensim.scripts.glove2word2vec import glove2word2vec
import sys
import gc
import pandas as pd
import spacy
import time
import textacy
import re
from multiprocessing import Pool
import nltk
from collections import defaultdict
from itertools import takewhile
from operator import itemgetter
import re
from numpy import nanmin, nanmax, zeros, NaN
import numpy as np
from spacy.parts_of_speech import CONJ, DET, NOUN, VERB
from spacy.tokens.span import Span as SpacySpan
from spacy.lang.en.stop_words import STOP_WORDS

import textacy
from textacy import spacy_utils, text_utils
from textacy.compat import unicode_
from textacy.spacy_utils import (normalized_str, get_main_verbs_of_sent,
                                 get_subjects_of_verb, get_objects_of_verb,
                                 get_span_for_compound_noun,
                                 get_span_for_verb_auxiliaries)
from textacy.constants import NUMERIC_NE_TYPES, REPORTING_VERBS
from wordcloud import WordCloud, ImageColorGenerator
import word2veckeras
pd.set_option('max_colwidth',-1)
pd.set_option('max_row',100)

a = time.time()

# 1. Data Preprocessing
- This part includes data importing and cleaning

In [2]:
#==================================   Import Data   =====================================
def read_reviews():
    """import reviews data
    """
    path = './real'
    appended_data = []

    for i, filename in enumerate(glob.glob(os.path.join(path, '*.csv'))):
        temp  = pd.read_csv(filename)
        appended_data.append(temp)  
    data = pd.concat(appended_data, ignore_index=True)
    return data

def read_opinions():
    """import opinions lexicon data 
    """
    lexico_p = pd.read_csv('./positive-words.txt',  
                           sep="\n", header = None)
    lexico_p.columns = ['opinion_words']
    lexico_p = lexico_p.loc[35:].reset_index(drop=True)
    set_p = set(lexico_p['opinion_words'])
    lexico_n = pd.read_csv('./negative-words.txt',  
                           sep="\n", header = None)
    lexico_n.columns = ['opinion_words']
    lexico_n = lexico_n.loc[34:].reset_index(drop=True)
    set_n = set(lexico_n['opinion_words'])
    opinions = set_n | set_p
    return opinions

#you can change the directory
reviews_data = read_reviews()
opinions = read_opinions()

In [3]:
##==============================  show data  ================================##
print(list(opinions)[:20])
print(reviews_data.loc[0])

['spurious', 'wrestle', 'dastardly', 'clamor', 'defame', 'indecency', 'wince', 'impudence', 'slowwww', 'delight', 'succeed', 'cramp', 'revulsion', 'choke', 'chic', 'rewardingly', 'bravado', 'deter', 'mendacious', 'unnatural']
name            GuinnessFan                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                           

In [4]:
##===================================   clean data   =======================================
#lot of cleaning here based on exploration
def replace(text):
    if type(text) is str:
        text = text.replace(' i ', ' I ')
        text = text.replace('<br />', ' ')
        text = text.replace('/', ' or ')
        text = text.replace('gonna', 'going to')
        text = text.replace('isn t', 'is not')
        text = text.replace('it s', 'it is')
        text = text.replace('like-it', 'like it')
        text = text.replace('love-it', 'love it')
        text = text.replace('aren t', 'are not')
        text = text.replace('can t', 'can not')
        text = text.replace('I like', 'I likes')
        text = text.replace('i like', 'i likes')
        text = text.replace('e like', 'we likes')
        text = text.replace('hey like', 'hey likes')
        text = text.replace('...', '.')
        text = text.replace('!!!', '!')
        if text.capitalize() == text:
            text = text.lower()   #transfer the Captatilize in 1st letter
        return text
    else:
        return 'NAN'

text = pd.DataFrame(columns=['text', 'tokens', 'pos'])    
text['text'] = reviews_data['review_text'].apply(replace)

# 2. Extract opinions
- We will use spacy for the POS work. For theac word in a sentence, we will tag the part of speech of them. Here is an example:

```
nlp = spacy.load('en_core_web_lg')
for x in nlp('Very good coffee taste'):
    print(x.pos_)

# ADV
# ADJ
# NOUN
# NOUN
```

- After POS tagging, we apply regular expression to extract phrases.
- After getting numourous phrases, we use lexicon to filter out the noise get meaning opinons only.[1]
- **This part is very time comsuming, you can also jumped to part 2, where the data is cleaned.**

#### Citation:
- [1]Hu, M. and Liu, B., 2004, August. Mining and summarizing customer reviews. In Proceedings of the tenth ACM SIGKDD international conference on Knowledge discovery and data mining (pp. 168-177). ACM.

In [6]:
#=====================================   word embedding   ==========================================
## RULES, EXAMPLE
## NOUN VERB ADJ ---> everything is ok
## NOUN VERB ADV ADJ ---> list is not correct
## NOUN VERB ADV ---> cars run fast
## NOUN VERB ADV( NOUN PRON VERB) ---> Clorets gum does
 
## ADJ PUNCT ADJ NOUN NOUN  ---> healthier, whole grain versions  
## ADJ NOUN NOUN --->  brown rice flour
## ADJ NOUN ADP NOUN ---> superior piece of equipment
## ADJ NOUN CCONJ NOUN ---> Great packing and speed
## VERB ADV VERB ---> do not buy
## PRON VERB VERB ---> I would recommend(过滤之后剩下recommend之类的金子, 筛掉沙子)
## VERB ADV ADV ADJ ADP ---> is not as good as
## ADV ADV ADJ ---> considerably more bland
## PRON ADV VERB ---> they absolutely love
## ((VERB PRON)|())?( ADV) ADJ PART VERB ---> (makes it/it is) very convenient to take out
## ADV ADV PRON VERB ---> how happily they munched on these
## VERB ADJ ADP( DET)?( ADJ)?( NOUN)?  ---> IS BETTER THAN 
## r'(VERB( PRON|( DET NOUN))? ADV)',   ---> I love it better
## VERB ADV ADJ ---> was so nasty
## NOUN', 'ADP', 'PRON -- > cats like it

   
def generate_phrase(tokens):
    print("="*90)
    res = []
    for sent in tokens.sents:
        if len(sent)<=3:  #etc, recommend! great!
            res.append(sent) 
        pos = [token.pos_ for token in sent]  #spaCy uses the dependency parse to determine sentence boundaries.
        pos_string = ' ' + ' '.join(pos)
        regexps = [
            r'((ADJ)? ADJ NOUN)',
            r'((ADV )?ADJ (NOUN|PROPN) ADP (NOUN|PROPN))',
            r'((ADV )?ADJ (NOUN|PROPN) CCONJ (NOUN|PROPN))',
            r'((ADV )?ADJ( PUNCT ADJ)?( CCONJ ADJ)? (NOUN|PROPN))',
            r'((ADV )?(ADJ PUNCT)?( ADJ CCONJ)? ADJ (NOUN|PROPN) (NOUN|PROPN))',
            r'(((NOUN|PROPN)( VERB)?( ADV)? ADJ( PUNCT ADJ)?( CCONJ ADJ)?))', 
            r'((PRON VERB ( ADV)? ADJ( PUNCT ADJ)?( CCONJ ADJ)?))', 
            r'(ADJ PUNCT ADJ CCONJ ADJ)',
            r'((NOUN|PROPN)? VERB ADV ADJ( PUNCT ADJ)?( CCONJ ADJ)?((DET)? (NOUN|PROPN))?)',
            r'((NOUN|PROPN)? VERB ADV ADJ( PUNCT ADJ)?( CCONJ ADJ)? PROUN)',
            r'((NOUN|PROPN) VERB ADV( (NOUN|PROPN) PRON VERB)?)',
            r'(VERB ADV ADV)',
            r'(VERB ADV VERB)',
            r'((ADV)? ADJ PART VERB ADJ( (NOUN|PROPN))?)',
            r'((ADV)? ADJ PART VERB(DET)? (NOUN|PROPN)?)',
            r'((ADV)? ADJ PART VERB( CCONJ VERB))',
            r'(VERB( PRON) ADV)',
            r'(VERB( DET (NOUN|PROPN))( CCONJ( DET)? (NOUN|PROPN))?( ADV)?)',
            r'(ADV VERB DET( (NOUN|PROPN))?)',
            r'(VERB ADV ADJ)',
            r'(PRON VERB( ADV)? VERB)',
            r'(VERB( ADV)? ADV ADJ ADP)',
            r'(ADV ADV ADJ)',
            r'(PRON ADV VERB( DET)?( (NOUN|PROPN))?)', 
            r'(VERB PRON( ADV)? ADJ PART VERB)',
            r'(VERB PRON PART VERB ADJ)',
            r'( ADV ADV PRON VERB)', 
            r'(PRON VERB PRON (ADV)?)',
            r'((VERB)? ADJ ADP( DET)?( ADJ)?( (NOUN|PROPN))?)', 
            r'((NOUN|PROPN) ADP( DET (NOUN|PROPN)))',
            r'((NOUN|PROPN) ADP( PRON))',
            r'(ADV ADP DET (NOUN|PROPN))', 
            r'(VERB ADP( ADV)?( NUM)? (NOUN|PROPN))',
            r'((VERB)? VERB VERB( ADV)?)', 
            r'(VERB VERB PART VERB( ADJ|NOUN))',
            r'(NUM (NOUN|PROPN) PART)',
            r'(VERB ADP DET (NOUN|PROPN))',
            r'((NOUN|PROPN) ADV ADV)',
            r'(ADV VERB PRON)',
            r'((ADV)? ADJ PUNCT)',
            r'(ADJ)? NOUN VERB PRON', 
            r'(VERB( PUNCT) NOUN)',
            r'ADJ ADP NOUN',
            r'ADV NOUN PRON VERB',
            r'ADJ CCONJ VERB ADJ',
        ]
        for regexp in regexps:
            p = re.compile(regexp)
            if not p.search(pos_string):
                continue
            else:
                x = pos_string[p.search(pos_string).span()[0]:p.search(pos_string).span()[1]] 
                for m in re.finditer(x, pos_string):
                    res.append(sent[pos_string[0:m.start()].count(' ')-1:pos_string[0:m.end()].count(' ')])
    return res

def extract_lexico(span):
    """
    @input: a list containing spans format, candidates1 phrases
    @output: a list containing strs
    For each token in span ,
    Lemmatize and then find if any in opinion set 
    """
    res = set()
    for x in span:
        if len(x)!=0: 
            for tk in nlp(x.lemma_): 
                if tk.text in opinions:
                    temp = []
                    for w in x:
                        if not w.is_punct and w.lemma_ != '-PRON-':
                            temp.append(w.lemma_)
                    res.add(' '.join(temp))
                    #no dif between "I love" and "my girlfriend love"
                    break
    return list(res)

nlp = spacy.load('en_core_web_lg')
text['tokens'] = text['text'].apply(lambda x: nlp(x))
text['candidates1'] = text['tokens'].apply(generate_phrase)

#candidate1--------------------->candidates2
#Example: I love the flavor -----> Love the flavor
text['candidates2'] = text['candidates1'].apply(extract_lexico)
text = text[['text', 'candidates1', 'candidates2']]

A: SENT------ This is the latest Keurig coffee maker.
A: SENT------ I bought it to replace my eight year old Keurig original model (the one with only two sizes and pretty much nothing else.)
A: SENT------ That machine held on just long enough to keep me from having to buy one of the over-engineered digital monstrosities that Keurig put out between this one and my first machine.
A: SENT------ There's plenty to like about this machine.
A: SENT------ First off, the aforementioned lack of digital gimmickry, and the wonderful accompanying blessing of no more nonsense about the K-cup not being on Keurig's list of approved kick-back brands of K-cups.
A: SENT------ Second, it DOES retain the great idea from the digital machines of a strong brew setting (which I absolutely love.)
A: SENT------ Third, it has four sizes which is maybe not earth-shaking, but is still kind of nice.
A: SENT------ One other tiny improvement over my original model is that the compartment stays all the way open instead

A: SENT------ As soon as it was plugged back in and turned on, it istarted pumping again.
A: SENT------ I contacted Keurig and have updated this review:
A: SENT------ I know that i'm late to the Keurig game
A: SENT------ but I never had the opportunity to see how they work until recently.
A: SENT------ I was so impressed with someone else's Keurig that I thought I'd buy one too.
A: SENT------ The ease of use and how fast I can have a single cup of whatever kind of coffee I want is amazing to me.
A: SENT------ The machine works great and it brings a whole new enjoyment to making coffee.
A: SENT------ I'm so happy with how this works at my house that I think I might just have to get another for my office.
A: SENT------ Pods are expensive but the convenience the machine offers and ability to brew one cup at a time is very nice.
A: SENT------ My son and I both have this model (K-Select) and they work quite well.
A: SENT------ The description of the Keurig K-Select Single Serve K-Cup Pod Co

A: SENT------ I still miss the Senseo maker.  
A: SENT------ This is easy to use.
A: SENT------ I have not tried the pods you fill yourself yet,
A: SENT------ that's next.
A: SENT------ I feel guilty using the plastic K- cups now.
A: SENT------ I don't think I'd buy another one due to the plastic waste.
A: SENT------ This is one of the quietest Keurig one cups I have owned.
A: SENT------ The strong feature is a great plus.
A: SENT------ I considered one of the touch screen versions but my father in law is not the type to learn new tech.
A: SENT------ So this one is a great compromise.
A: SENT------  It works perfect really nice red I am using Sam's brand coffee and not problem at all I love it.
A: SENT------ Love this Keurig; perfect size, fabulous color & easy to use.
A: SENT------ I have had several Keurig machines in the past, and they've all been pretty crappy.  
A: SENT------ Takes too long, coffee is not hot enough..and the machines don't last worth  darn.  
A: SENT------ This ne

A: SENT------ We have been using Keurig K-Cup Single Cup coffee-makers for years.
A: SENT------ This review is for the K-Elite in brushed slate.
A: SENT------ I had two choices in target - pay $129 for an identical coffee maker without an iced coffee button  or $169 for this one.
A: SENT------ Because I made a lot of iced coffees and teas in my original keurig (smaller version)
A: SENT------ I opted to pay more for the iced coffee button.
A: SENT------ I thought that it would brew at a different temperature, but it's identical to any other kind of brew process.
A: SENT------ You can do this with any keurig - you just fill a cup with ice, the "iced coffee or tea" brews hot and then is cooled down by the ice.
A: SENT------ What the iced button does it make it a "small" so that it fits in a cup with ice.
A: SENT------ However you do not need to spend any extra money on this feature and I am quite disappointed in Keurig for marketing it this way.
A: SENT------ The iced button is misleading

A: SENT------ THEN....hit the little round button.  
A: SENT------ Would help to read the instructions first lol  
A: SENT------ I almost thought I got a dud..
A: SENT------ but it was just me :)  
A: SENT------ Nice little coffee
A: SENT------ maker.but then again I've always loved my Keurigs!
A: SENT------ Amazon was their usual perfect fast shipping..
A: SENT------ so all good!
A: SENT------ Nothing but trouble until it broke in less than a week!  
A: SENT------ I have invested way too much in pods, carafe, drawer, scooper, filters etc and now they are sending me a replacement machine!  
A: SENT------ Tried a keurig pod and grounds got into the machine and took me hours to clean it out only for it to happen again.  
A: SENT------ Cold coffee, weak and the smallest little cup for over a dollar for 4 ounces.  
A: SENT------ I clearly did not do my homework before investing.
A: SENT------ I just received my Keurig in the color "oasis".
A: SENT------ I'm absolutely enamored with it!
A: 

...

A: SENT------ Constant brews interrupted, coffee grounds in almost every cup, constantly wasting k-cups.  
A: SENT------ Going back to a normal coffee machine after several years of using Keurig thanks to this horrendous garbage machine.
A: SENT------ So far so good.  
A: SENT------ We have purchased the Cuisinart for the past 8 years and haven't had too much luck with them.  
A: SENT------ This one we did purchase the warranty with.
A: SENT------ So awesome!
A: SENT------ This thing is a game changer for mornings.
A: SENT------ Honestly actually makes life about 10% more fun to live (if you love coffee and tea like I do.)
A: SENT------ I just wear these out as I just keep buying
A: SENT------ We have owned several Keurigs over the years but this tops.
A: SENT------ Love the extra strong button and it really does add to your coffee.
A: SENT------ We loved this Keurig when we got it just before Christmas.
A: SENT------ But a couple weeks ago, after a month or so of use, it istopped work

A: SENT------ I bought another one from another store and it works great so the 575
A: SENT------ I would highly recommend
A: SENT------ Love Love Love our Keurig.
A: SENT------ This is our first and its the best
A: SENT------ works great, makes good coffee.
A: SENT------ Love my Keurig
A: SENT------ Fast, easy, convenient.  
A: SENT------ It is a little larger than expected, but still works out very well for us.  
A: SENT------ Both of us can have what we what, when we want it and as often as we want.
A: SENT------ mother in law loves it
A: SENT------ set it up and it is great.
A: SENT------ awesome
A: SENT------ convient and easy to use.
A: SENT------ Saves me so much time in the morning!
A: SENT------ I don't have to wait at the coffee shop any more!
A: SENT------ Fantastic replacement for my old Keurig Classic system!
A: SENT------ NEVER WORKED.
A: SENT------ I WOULD SEND BACK
A: SENT------ BUT TOO LATE.
A: SENT------ A PIECE OF JUNK
A: SENT------ works well, as advertised.
A: SENT

A: SENT------ ill probably take it to the range and use it for target practice.
A: SENT------ junk.  
A: SENT------ ill never buy another Keurig.
A: SENT------ I m growing increasingly frustrated with this machine.
A: SENT------ Yes, it istill works.barely.
A: SENT------ I have had issues with it isince we bought it about a year ago.
A: SENT------ It takes several attempts to engage the brew setting when lowering the handle.
A: SENT------ It is VERY loud while brewing.
A: SENT------ It shuts off at will.
A: SENT------ It s own will.
A: SENT------ I love the brand but the more bells and whistles you have on one, the less it functions as it ishould.
A: SENT------ Be savvy.
A: SENT------ get one with less functionality and more practicality.
A: SENT------ Love the coffee maker.
A: SENT------ It's used almost every single day.
A: SENT------ sometimes twice or more in a day.
A: SENT------ So far quite happy with it.
A: SENT------ so far happy with this machine, hot coffee, good variety of k

A: SENT------ but I likes my coffee more.
A: SENT------ Very disappointing.after a few brews it would flash a high pressure warning and say needle maintenance required.
A: SENT------ Never had that on our old keurig.
A: SENT------ Called customer service and a very nice woman walked me through what needed to be done.
A: SENT------ After that no problems for a few weeks.
A: SENT------ I would use the special needle cleaner to clean it once a week and would brew a cup of water before and after each cup of coffee to ensure everything was cleaned out.
A: SENT------ But it is ridiculous to pay that much for a coffee maker to have so many problems and maintenance issues with it.
A: SENT------ I have wasted just as many k cups as I have brewed with this machine and no matter how much I service it (exactly as keurig tells me to)
A: SENT------ it istill is hit and miss on a successful brew.
A: SENT------ Would not recommend.save your money.
A: SENT------ Apparently, "Keurig" is supposed to mean

A: SENT------ The pump makes a lot of noise and it makes you select the cup serving size every time you switch flavors.  
A: SENT------ I have 3 of these boat anchors.
A: SENT------ 2 at work and 1 at home
A: SENT------ and I can notell you, its a over priced piece of junk.
A: SENT------ I trashed the home unit and bought a superior competing brand that is very quiet and painless to use.
A: SENT------ Keurig  will not see another machine coming to my locations.  
A: SENT------ AND - What the heck is the phone jack plug in the bottom of the unit for?
A: SENT------ It must call 911 when you stroke out trying to milk this cow for some coffee.
A: SENT------ Mine is for sale.
A: SENT------ 20.00 plus shipping
A: SENT------ and you can have it.
A: SENT------ 2nd thought, Discounted - send me 20.00
A: SENT------ and I UPS it to you.
A: SENT------ Well OK - send me your pity party story.
A: SENT------ The person with a life sorrier than this machine wins it for free.
A: SENT------ I purchased 

In [7]:
# text.to_csv('./phrases.csv', index=False)
text.head(3)

text  \
0  This is the latest Keurig coffee maker. I bought it to replace my eight year old Keurig original model (the one with only two sizes and pretty much nothing else.) That machine held on just long enough to keep me from having to buy one of the over-engineered digital monstrosities that Keurig put out between this one and my first machine. There's plenty to like about this machine. First off, the aforementioned lack of digital gimmickry, and the wonderful accompanying blessing of no more nonsense about the K-cup not being on Keurig's list of approved kick-back brands of K-cups. Second, it DOES retain the great idea from the digital machines of a strong brew setting (which I absolutely love.) Third, it has four sizes which is maybe not earth-shaking, but is still kind of nice. One other tiny improvement over my original model is that the compartment stays all the way open instead of springing back down a littlwe likes the handle did on my old machine, which is obviously a pretty minor consideration, but one I appreciate to a disproportionate degree.   
1  There appears to be a design or manufacturing flaw in this coffee maker.  Amazon Customer Service have been really good about replacing units, but I am now getting a 3rd unit ishipped to me (at no additional cost, I might add).  The first 2 units have the same problem:  Water flows into the cup before any cup-size button has been pressed, and the water is cold.  Maybe the 3rd unit will be okay, but I'm not confident that it will be.  ***Update:  The 3rd unit malfunctions just like the other two.  Unless the manufacturer can convince you that they have fixed the problem, stay away from this model.***                                                                                                                                                                                                                                                                                                                                                                                                                                                                          
2  Prior to this new Keurig, my favorite K-Cup machine was the Cuisinart SS-700.  Recently Cuisinart replaced the SS-700 with the poorly engineered flimsy SS-10 model, which I returned because it tends to spray coffee all over the place.                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                              

                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                   

# 3. Semantic similarity calculation and clustering
- The final method id word mebedding + Word Mover's Distance(https://vene.ro/blog/word-movers-distance-in-python.html)  
- We used Glove and Word2vec embedding models. **Before running the following model, you need to download to the two models into a folder called 'pretrained' in the current directory**. The models can be found here.https://drive.google.com/open?id=1bvJLlbqN0iSTGiZ7a3v0DUKfnWPXja-V


```
##citation: 
- https://en.wikipedia.org/wiki/Word_embedding
- https://en.wikipedia.org/wiki/Word2vec
- https://nlp.stanford.edu/projects/glove/

# * `Ofir Pele and Michael Werman "A linear time histogram metric for improved SIFT matching"
#   <http://www.cs.huji.ac.il/~werman/Papers/ECCV2008.pdf>`_
# * `Ofir Pele and Michael Werman "Fast and robust earth mover's distances"
#   <https://ieeexplore.ieee.org/document/5459199/>`_
# * `Matt Kusner et al. "From Word Embeddings To Document Distances"
#   <http://proceedings.mlr.press/v37/kusnerb15.pdf>`_.
```

In [11]:
#=================================   Data Preprocessing again  ===================================
#1. import the preprocessed data
text = pd.read_csv('./phrases_new.csv')

#2. phrase the data we have
def collect_phrases(string):
    return re.findall("\'(.*?)\'", string[1:-1])

def process(phrases):
    res = []
    for x in phrases['phrases']:
        res += x 
    cnt = Counter(res)
    res = pd.DataFrame(res, columns=['phrases'])
    res['count'] = res['phrases'].apply(lambda x:cnt[x])
    # drop the very short phrases
    res['length'] = res['phrases'].apply(len)
    res = res.sort_values(by = 'length', ascending=False)
    res = res[res['length'] > 6]   
    res = res.reset_index(drop=True)

    res = res.drop_duplicates(keep='first', inplace=False)
    res = res.sort_values(by = 'count', ascending=False)
    res = res.reset_index(drop=True)
    return res

text['phrases'] = text['candidates2'].apply(collect_phrases)
total_phrases = text[['product_id', 'phrases']]

#pick which product to 
phrases = total_phrases[total_phrases['product_id']==5]
opinion_phrases = process(phrases)
del text, phrases, total_phrases
gc.collect()

554

In [12]:
#=================================   Compare Similarity of phrases   ===================================

# 1. Load pretrained model：glove&word2vec
model_w2v = KeyedVectors.load_word2vec_format(
    './pretrained_model/GoogleNews-vectors-negative300.bin', binary=True)

# we can also use the glove embedding
# glove_input_file = './pretrained_model/glove.840B.300d.txt'
# word2vec_output_file = './pretrained_model/glove.840B.300d.txt.word2vec'
# glove2word2vec(glove_input_file, word2vec_output_file)

# model_glove = KeyedVectors.load_word2vec_format(
#     './pretrained_model/glove.840B.300d.txt.word2vec', binary=False)

In [ ]:
##============================= make the semantic distance matric ======================

# multi threshold will be used here 
# since the calculation to too large(up to 7 hours for the largest product)
def f(i):
    return [0] * i + [model_w2v.wmdistance(
        opinion_phrases['phrases'][i], opinion_phrases['phrases'][j]
    ) for j in range(i, opinion_phrases.shape[0])]
with Pool(7) as p:
    p_res = p.map(f, range(opinion_phrases.shape[0]))
similarity_matrix_w2v = np.array(p_res)

In [ ]:
##======================  clustering result and make visualization  =======================##

def generate_wc(fname, df):
    #prepare for visualization
    frequency = df.set_index('phrases', drop = True).to_dict()['total_count']
    
    # Generate a word cloud image
    picture  =WordCloud(width=1000, height=600, margin=2)
    wordcloud = picture.generate_from_frequencies(frequency)
    plt.figure(figsize=(18, 12))
    plt.imshow(wordcloud, interpolation="kaiser")
    plt.axis("off")
#     plt.savefig("results/product_5_wordcloud.png")
    plt.suptitle(fname, fontsize=30)
    plt.show()

def make_clusters(km):
    clusters_w2v_km = km.fit_predict(similarity_matrix_w2v)
    clusters = pd.DataFrame(clusters_w2v_km, columns=['clusters'])

    phrases_new = pd.concat([res, clusters], axis=1)

    temp = phrases_new.groupby('clusters')['count'].sum()
    temp = temp.to_frame(name='total_count')
    temp = temp.reset_index(drop = False)

    final_result = phrases_new.drop_duplicates(subset='clusters', keep='first', inplace=False)
    final_result = final_result.reset_index(drop=True)
    final_result = final_result.merge(temp)
    return final_result

km = cluster.KMeans(n_clusters=100, precompute_distances=True)
final_result = make_clusters(km)
generate_wc('word_cloud_glove',final_result[['phrases', 'total_count']])

del clusters_w2v_km, clusters, temp
gc.collect()

In [ ]:
# final_result.to_csv('results/result_product_5.csv')
final_result

# 4. Result analysis and Hypothesis Test
- From the final_result we obtained above, we can find for product 5, out 100, phrases of number "3, 11, 42, 63, 64, 70, 71, 77, 82, 87, 96, ", i.e."a long time, or cold, really like the, boost be call, etc." are not semantically revelent to the product. Which means the accuracy is . Also we can get all the accuracies for two models and all nine products.
- Paired/dependent T test are used for the nine data points here.
- The dataframe are accuracies we obtained
- code citation:https://pythonfordatascience.org/paired-samples-t-test-python/

In [ ]:
from statsmodels.stats.power import TTestIndPower
from scipy import  stats
d = {'accuracy_w2v': [0.92, 0.91,0.87,0.85,0.9,0.89,0.8,0.91,0.91], 
     'accuracy_glove': [0.91, 0.9, 0.91,0.87,0.88,0.91,0.87,0.86,0.86]
    }

df = pd.DataFrame(data=d)
df.describe()

### 4.1 Check Assumptions
- 1.Outliers: from the boxplot, we can find there is no outliers.
- 2.Normal Distribution: From the QQ-PLOT, we can find the difference follows the normal distribution.

In [ ]:
##========================== check 1. Outliers =============================##
df.plot(kind='box')
# This saves the plot as a png file
plt.savefig('boxplot_outliers.png')

In [ ]:
##========================== check 2. Normal Distributions =============================##
df['acc_difference'] = df['accuracy_w2v'] - df['accuracy_glove']
stats.probplot(df['acc_difference'], plot= plt)
plt.title('Accuracy Difference Q-Q Plot')
plt.savefig('Accuracy difference qq plot.png')

stats.shapiro(df['acc_difference'])
#The first value is the W test value, and the second value it the p-value. We can find the test is non-significant(p_value=0.68)


### 4.2 Hypostheis test and Power analysis
- Total there will be nine pairs of data point, after power analysis, when the effect size is 1.4, and significance level of 0.05, we can be 80% claim our experiments are reliable. 
- The null hypothesis is that there is no difference between accuracies between the two methods, while the alternative hypothesis is there is some difference. Statics of paired sample t test will be utilized here. After assumption check and hypothesis test, we got the p-value of 0.936, which is much larger than 0.05, the significance level, so that we do not reject null hypothesis and conclude that there is no significant difference between the accuracies between clustering models based on word2vec and glove embeddings.


In [ ]:
##========================== Hypothesis Test  =============================##
stats.ttest_rel(df['accuracy_w2v'], df['accuracy_glove'])
# WE find pvalue is very big, means we cannot reject H0. So we can not claim there is difference between two accuracies.


In [ ]:
# parameters for power analysis
effect = 1.5
alpha = 0.05
power = 0.8
# perform power analysis
analysis = TTestIndPower()
result = analysis.solve_power(effect, power=power, nobs1=None, ratio=1.0, alpha=alpha)
print('Sample Size: %.3f' % result)